In [24]:
import pandas as pd
import pydeck as pdk
import folium
import sys
from pathlib import Path
import json
import plotly.express as px

import os

sys.path.append(str(Path(os.getcwd()).parent))

from lib.constants import DATA_DIR

In [26]:
with open(DATA_DIR/'osuked/wind_farm_data.json') as f:
    wind_farm_dict = json.load(f)

In [27]:
wind_farm_dict.keys()

dict_keys(['Nationaldataset', 'WindFarms', 'Winds'])

In [28]:
# wind_farm_dict["WindFarms"] += wind_farm_dict["Winds"]

In [29]:
wind_farm_dict["WindFarms"]

[{'Id': 'RREW-1',
  'Name': 'Robin Rigg East',
  'Latitude': '54.763880',
  'Longitude': '-3.697027',
  'OutputPercentage': '8.89%',
  'Output': '8.0',
  'WindFarmImage': None,
  'Coordinates': '"-3.67755299999993,54.7522050000001", "-3.69013699999994,54.74431", "-3.69183702899994,54.7447469420001", "-3.70505799999995,54.7481450000001", "-3.70505665599995,54.748146654", "-3.70173299999993,54.752237", "-3.73993699999994,54.76293", "-3.68454199999996,54.782793", "-3.66930799999994,54.772748", "-3.67755299999993,54.7522050000001"',
  'PolygonOverlay': '',
  'Operator': 'EON C&R UK Robin Rigg East Ltd',
  'OperatorLogoLarge': None,
  'OperatorLogoSmall': None,
  'NumberOfTurbines': '30',
  'TurbineTypeBrand': '',
  'TurbineTypeModel': 'V90-3.0 MW',
  'OperatorWebsite': '',
  'OperatorWebsiteLabel': '',
  'WindFarmLocationImage': None,
  'TurbineCordinates': '"-3.70051665399995,54.7714999990001"; "-3.69344998799994,54.769916666"; "-3.70933332199996,54.7691666650001"; "-3.70313331999995,54.7

In [30]:
all_farms = {}
for farm in wind_farm_dict["WindFarms"]:
    id_ = farm.get('Id', hash(( farm['Latitude'], farm['Longitude'])))
    all_farms[id_] = {"lat": farm['Latitude'], "lng": farm['Longitude']}

In [31]:
len(all_farms)

43

In [32]:
m = folium.Map(location=[54.763880, -0])
for farm_id, coords in all_farms.items():
    folium.Marker(
    [coords['lat'], coords['lng']], popup=f"<b>{farm_id}</b>"
    ).add_to(m)


In [33]:
m

I think we may be missing a lot of onshore wind?

# Square this with curtailment

In [87]:
df_curtailment = pd.read_feather(DATA_DIR/"outputs/curtailment-2022-01-01-2022-02-01.fthr")

In [95]:
downsampled = []
for unit, data in df_curtailment.groupby("unit"):
    data = data.set_index("Time")
    data = data.resample("H").sum().reset_index()
    data['unit'] = unit
    downsampled.append(data)

In [96]:
px.line(pd.concat(downsampled), x='Time', y='delta', color='unit')

In [38]:
wind_farm_ids = [farm['Id'] for farm in wind_farm_dict["WindFarms"]]
sorted(wind_farm_ids)

['ABRDB',
 'BODW-1',
 'BOWLW-1',
 'BRBEO-1',
 'BTRIC',
 'BURBW-1',
 'DDGNO',
 'EA-1',
 'GAOFO',
 'GNFSW-1',
 'GNFSW-2',
 'GRGBW',
 'GYMRW',
 'HMGTO',
 'HOWAO',
 'HYWND',
 'INNDW-1',
 'KENT-1',
 'KENT-2',
 'KNCRD',
 'LARYO',
 'LNCSW',
 'LYNNW-1',
 'METHL',
 'MORY-E',
 'NHOYW-1',
 'OMNDO-1',
 'RCBKO',
 'RHYFW-1',
 'RMPNO',
 'RREW-1',
 'RRWW-1',
 'SCRO-1',
 'SHRSO',
 'TEES-1',
 'THNTW',
 'TRTNK',
 'WDNSW',
 'WLNYO-2',
 'WLNYO-3',
 'WLNYO-4',
 'WLNYW-1',
 'WTMSO-1']

These don't seem to be the same thing as the BM unit ids :) 

In [37]:
df_curtailment['unit'].unique()

array(['2__PSTAT001', 'E_ABRTW-1', 'E_ASHWW-1', 'E_BABAW-1', 'E_BRDUW-1',
       'E_BRYBW-1', 'E_BTUIW-2', 'E_DALSW-1', 'E_GLOFW-1', 'E_MOYEW-1',
       'T_AKGLW-2', 'T_AKGLW-3', 'T_ARCHW-1', 'T_BEATO-1', 'T_BEATO-2',
       'T_BEATO-3', 'T_BEATO-4', 'T_BHLAW-1', 'T_BLLA-1', 'T_BLLA-2',
       'T_BRBEO-1', 'T_CGTHW-1', 'T_CLDCW-1', 'T_CLDNW-1', 'T_CLDSW-1',
       'T_CRDEW-1', 'T_CRDEW-2', 'T_CRGHW-1', 'T_CRMLW-1', 'T_CRYRW-2',
       'T_DNLWW-1', 'T_DOREW-1', 'T_DOREW-2', 'T_DRSLW-1', 'T_DUNGW-1',
       'T_EAAO-1', 'T_EAAO-2', 'T_EDINW-1', 'T_EWHLW-1', 'T_FALGW-1',
       'T_FARR-1', 'T_FARR-2', 'T_FSDLW-1', 'T_GLWSW-1', 'T_GORDW-1',
       'T_GORDW-2', 'T_GRGBW-1', 'T_GRGBW-2', 'T_GRIFW-1', 'T_GRIFW-2',
       'T_HADHW-1', 'T_HOWAO-1', 'T_HOWAO-2', 'T_HOWAO-3', 'T_HRSTW-1',
       'T_KILBW-1', 'T_KLGLW-1', 'T_KPMRW-1', 'T_LARYW-1', 'T_LARYW-2',
       'T_LARYW-3', 'T_LARYW-4', 'T_MIDMW-1', 'T_MILWW-1', 'T_MKHLW-1',
       'T_MOWEO-2', 'T_MYGPW-1', 'T_PNYCW-1', 'T_RCBKO-1', 'T_RCBKO-

In [39]:
data_dict = pd.read_csv(DATA_DIR/"osuked/dictionary_attributes.csv")

In [45]:
data_dict[data_dict["id_type"]=="ngc_bmu_id"]


attribute       id                value  \
0                  Fuel Type   MARK-1              BIOMASS   
1                  Fuel Type   MARK-2              BIOMASS   
4        Annual Output (MWh)   MARK-1           355704.933   
5        Annual Output (MWh)   MARK-1           387311.364   
6        Annual Output (MWh)   MARK-1           295847.593   
...                      ...      ...                  ...   
10140  Capture Price (£/MWh)  WHIHW-1    32.61252424949882   
10141            Load Factor  WHIHW-1  0.41674226507770523   
10142            Load Factor  WHIHW-1   0.4124691878716266   
10143            Load Factor  WHIHW-1  0.42643697689484367   
10144              Fuel Type  WTGRW-1                 WIND   

                                             datapackage     id_type    year  \
0      https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id     NaN   
1      https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id     NaN   
4      https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2016.0   
5      https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2017.0   
6      https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2018.0   
...                                                  ...         ...     ...   
10140  https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2020.0   
10141  https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2019.0   
10142  https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2020.0   
10143  https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id  2021.0   
10144  https://raw.githubusercontent.com/OSUKED/Dicti...  ngc_bmu_id     NaN   

       dictionary_id  financial_year  
0              10000             NaN  
1              10000             NaN  
4              10000             NaN  
5              10000             NaN  
6              10000             NaN  
...              ...             ...  
10140          10310             NaN  
10141          10310             NaN  
10142          10310             NaN  
10143          10310             NaN  
10144          10311             NaN  

[5141 rows x 8 columns]

In [47]:
data_dict[data_dict["dictionary_id"]==10000]


attribute      id               value  \
0               Fuel Type  MARK-1             BIOMASS   
1               Fuel Type  MARK-2             BIOMASS   
2               Longitude   10000           -3.603516   
3                Latitude   10000           57.480403   
4     Annual Output (MWh)  MARK-1          355704.933   
5     Annual Output (MWh)  MARK-1          387311.364   
6     Annual Output (MWh)  MARK-1          295847.593   
7     Annual Output (MWh)  MARK-1          389670.228   
8     Annual Output (MWh)  MARK-1          347661.617   
9   Capture Price (£/MWh)  MARK-1   39.59720856417994   
10  Capture Price (£/MWh)  MARK-1   45.39047277322623   
11  Capture Price (£/MWh)  MARK-1  56.825873243072294   
12  Capture Price (£/MWh)  MARK-1   42.16549582086605   
13  Capture Price (£/MWh)  MARK-1    34.8285267211038   
14            Load Factor  MARK-1  0.7956421203195724   
15            Load Factor  MARK-1  0.7706435782539418   
16            Load Factor  MARK-1  0.8515695437114246   
17            Load Factor  MARK-1  0.7801021988866973   
18            Load Factor  MARK-1  0.8567559051943716   
19            Load Factor  MARK-1  0.7950629527945471   
20            Load Factor  MARK-1  0.8788488318816613   

                                          datapackage        id_type    year  \
0   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id     NaN   
1   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id     NaN   
2   https://raw.githubusercontent.com/OSUKED/Dicti...  dictionary_id     NaN   
3   https://raw.githubusercontent.com/OSUKED/Dicti...  dictionary_id     NaN   
4   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2016.0   
5   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2017.0   
6   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2018.0   
7   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2019.0   
8   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2020.0   
9   https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2016.0   
10  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2017.0   
11  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2018.0   
12  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2019.0   
13  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2020.0   
14  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2015.0   
15  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2016.0   
16  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2017.0   
17  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2018.0   
18  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2019.0   
19  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2020.0   
20  https://raw.githubusercontent.com/OSUKED/Dicti...     ngc_bmu_id  2021.0   

    dictionary_id  financial_year  
0           10000             NaN  
1           10000             NaN  
2           10000             NaN  
3           10000             NaN  
4           10000             NaN  
5           10000             NaN  
6           10000             NaN  
7           10000             NaN  
8           10000             NaN  
9           10000             NaN  
10          10000             NaN  
11          10000             NaN  
12          10000             NaN  
13          10000             NaN  
14          10000             NaN  
15          10000             NaN  
16          10000             NaN  
17          10000             NaN  
18          10000             NaN  
19          10000             NaN  
20          10000             NaN

Our unit ID's dont seem to be in this data dictionary thing either, I think because we're using `sett` not `ngc`

In [51]:
for unit_id in df_curtailment['unit'].unique():
    print(data_dict[data_dict["id"]==unit_id])

Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_type, year, dictionary_id, financial_year]
Index: []
Empty DataFrame
Columns: [attribute, id, value, datapackage, id_

In [52]:
def convert_sett_to_ngc_id(id_: str) -> str:
    return id_.split("_")[1]

Yep this works.

In [58]:
for unit_id in df_curtailment['unit'].unique():
    is_present = len(data_dict[data_dict["id"]==convert_sett_to_ngc_id(unit_id)]) > 0
    print(unit_id, is_present)

2__PSTAT001 False
E_ABRTW-1 True
E_ASHWW-1 True
E_BABAW-1 True
E_BRDUW-1 True
E_BRYBW-1 True
E_BTUIW-2 True
E_DALSW-1 True
E_GLOFW-1 True
E_MOYEW-1 True
T_AKGLW-2 True
T_AKGLW-3 True
T_ARCHW-1 True
T_BEATO-1 True
T_BEATO-2 True
T_BEATO-3 True
T_BEATO-4 True
T_BHLAW-1 True
T_BLLA-1 True
T_BLLA-2 True
T_BRBEO-1 True
T_CGTHW-1 True
T_CLDCW-1 True
T_CLDNW-1 True
T_CLDSW-1 True
T_CRDEW-1 True
T_CRDEW-2 True
T_CRGHW-1 True
T_CRMLW-1 True
T_CRYRW-2 True
T_DNLWW-1 True
T_DOREW-1 True
T_DOREW-2 True
T_DRSLW-1 True
T_DUNGW-1 True
T_EAAO-1 True
T_EAAO-2 True
T_EDINW-1 True
T_EWHLW-1 True
T_FALGW-1 True
T_FARR-1 False
T_FARR-2 False
T_FSDLW-1 True
T_GLWSW-1 True
T_GORDW-1 True
T_GORDW-2 True
T_GRGBW-1 True
T_GRGBW-2 True
T_GRIFW-1 True
T_GRIFW-2 True
T_HADHW-1 True
T_HOWAO-1 True
T_HOWAO-2 True
T_HOWAO-3 True
T_HRSTW-1 True
T_KILBW-1 True
T_KLGLW-1 True
T_KPMRW-1 True
T_LARYW-1 False
T_LARYW-2 False
T_LARYW-3 False
T_LARYW-4 False
T_MIDMW-1 True
T_MILWW-1 True
T_MKHLW-1 True
T_MOWEO-2 True
T_MYGPW

And yet even after applying this conversion, only 3 of our IDs are present on the map

In [57]:
set(wind_farm_ids).intersection(set([convert_sett_to_ngc_id(id_) for id_ in df_curtailment['unit'].unique()]))

{'BRBEO-1', 'WLNYO-3', 'WLNYO-4'}

So it looks like we need to get coords from this data dict monstrosity

In [77]:
def get_coords_from_data_dict(sett_id: str) -> dict:
    ngc_id = convert_sett_to_ngc_id(sett_id)
    entries = data_dict[data_dict['id'] == ngc_id]
    print(entries['attribute'].unique())
    if len(entries) > 0:
        return dict(lat=entries.loc[entries['attribute']=='Latitude', "value"],
               lng = entries.loc[entries['attribute']=='Longitude', "value"])
    return None
    

In [78]:
output = {}
for unit in df_curtailment['unit'].unique():
    output[unit]=get_coords_from_data_dict(unit)

[]
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel Type' 'Annual Output (MWh)' 'Capture Price (£/MWh)' 'Load Factor']
['Fuel 

In [79]:
output

{'2__PSTAT001': None,
 'E_ABRTW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_ASHWW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_BABAW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_BRDUW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_BRYBW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_BTUIW-2': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_DALSW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_GLOFW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], Name: value, dtype: object)},
 'E_MOYEW-1': {'lat': Series([], Name: value, dtype: object),
  'lng': Series([], 

Unfortunately the lat/lng don't seem to be there either!

# Hacks
If we have all the wind units, we expect there to be a bimodal distribution with the stuff north of B6 being curtailed and everything below not...

In [90]:
by_unit = df_curtailment.groupby('unit').sum().reset_index()
px.histogram(by_unit, x='delta', nbins=100)


In [97]:
px.bar(by_unit, x='delta', y='unit')